In [1]:
!pip install -q phonemizer torch transformers scipy munch gradio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.6/162.6 kB 7.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.8/103.8 kB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 MB 14.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 321.4/321.4 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.8/94.8 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.3/11.3 MB 59.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.3/62.3 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 47.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.9/59.9 kB 3.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.4/213.4 kB 10.7 MB/s eta 0:00:00
   ━━━━━

In [2]:
!git lfs install
!git clone https://huggingface.co/hexgrad/Kokoro-82M
%cd Kokoro-82M
!apt-get -qq -y install espeak-ng > /dev/null 2>&1

Git LFS initialized.
Cloning into 'Kokoro-82M'...
remote: Enumerating objects: 131, done.
remote: Counting objects: 100% (127/127), done.
remote: Compressing objects: 100% (127/127), done.
remote: Total 131 (delta 57), reused 0 (delta 0), pack-reused 4 (from 1)
Receiving objects: 100% (131/131), 57.13 KiB | 14.28 MiB/s, done.
Resolving deltas: 100% (57/57), done.
Filtering content: 100% (17/17), 820.18 MiB | 50.83 MiB/s, done.
/content/Kokoro-82M


In [3]:
from models import build_model
import torch
from kokoro import generate

In [4]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
MODEL = build_model('kokoro-v0_19.pth', device)

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
/usr/local/lib/python3.10/dist-packages/torch/nn/modules/rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(


In [5]:
# Language is determined by the first letter of the VOICE_NAME:
# 🇺🇸 'a' => American English => en-us
# 🇬🇧 'b' => British English => en-gb

VOICE_NAME = [
    'af', # Default voice is a 50-50 mix of Bella & Sarah
    'af_bella', 'af_sarah', 'am_adam', 'am_michael',
    'bf_emma', 'bf_isabella', 'bm_george', 'bm_lewis',
    'af_nicole', 'af_sky',
][0]
VOICEPACK = torch.load(f'voices/{VOICE_NAME}.pt', weights_only=True).to(device)
print(f'Loaded voice: {VOICE_NAME}')

Loaded voice: af


# Test

In [12]:
text = """Large language models like GPT-4 and LLaMA have demonstrated impressive abilities in generating coherent and contextually relevant text. However, they often struggle with complex reasoning tasks, leading to issues such as hallucinations (confidently asserting incorrect information) and shallow reasoning. Addressing these challenges is important for applications that require reliable and accurate responses.
A recent approach proposes using entropy measurements during the decoding process to guide the model’s token selection more effectively. By incorporating entropy and varentropy (variance of entropy), the model becomes more aware of its uncertainty, leading to more accurate and coherent outputs. This method, implemented in the Entropix project, aims to simulate chain-of-thought reasoning during inference by adjusting the sampling strategy based on the model’s confidence levels. So basically we built chain-of-thought into the model (which I think is a great idea)."""

audio = []
for chunk in text.split("."):
  print(chunk)
  if len(chunk) < 2:
    continue
  snippet, out_ps = generate(MODEL, chunk, VOICEPACK, lang=VOICE_NAME[0])
  audio.extend(snippet)

Large language models like GPT-4 and LLaMA have demonstrated impressive abilities in generating coherent and contextually relevant text
 However, they often struggle with complex reasoning tasks, leading to issues such as hallucinations (confidently asserting incorrect information) and shallow reasoning
 Addressing these challenges is important for applications that require reliable and accurate responses

A recent approach proposes using entropy measurements during the decoding process to guide the model’s token selection more effectively
 By incorporating entropy and varentropy (variance of entropy), the model becomes more aware of its uncertainty, leading to more accurate and coherent outputs


 This method, implemented in the Entropix project, aims to simulate chain-of-thought reasoning during inference by adjusting the sampling strategy based on the model’s confidence levels
 So basically we built chain-of-thought into the model (which I think is a great idea)



##### Display the 24khz audio

In [10]:
from IPython.display import display, Audio
display(Audio(data=audio, rate=24000, autoplay=True))

# Gradio-UI

In [6]:
from IPython.display import display, Audio
import numpy as np
import gradio as gr

def textSpeech(text):
  audio = []
  rate=22000
  for chunk in text.split("."):
    if len(chunk) < 2:
      continue
    snippet, out_ps = generate(MODEL, chunk, VOICEPACK, lang=VOICE_NAME[0])
    print(snippet)
    audio.extend(snippet)

  audio = np.array(audio, dtype=np.float32)
  return rate, audio

In [7]:
text = gr.TextArea(label="Text", max_lines=20, placeholder="Put your text here...")
output = gr.Audio(label="Generated Audio", type="numpy")
demo = gr.Interface(
    fn=textSpeech,
    inputs=text,
    outputs=output,
    title="Text to Speech"
)

demo.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://798d4163ef3e06a4b6.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


[-2.9370855e-07  2.1724144e-07  1.6649066e-07 ... -5.8851708e-07
  3.2399930e-07  7.2157195e-07]
[-1.15044806e-07  6.77326852e-08  9.96950931e-08 ... -7.20719342e-08
 -4.26061320e-08  6.27956013e-07]


/usr/local/lib/python3.10/dist-packages/gradio/processing_utils.py:738: UserWarning: Trying to convert audio automatically from float32 to 16-bit int format.
  warnings.warn(warning.format(data.dtype))


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://798d4163ef3e06a4b6.gradio.live
